### Imports

In [1]:
import pandas as pd
from datetime import timedelta
from datetime import datetime as dt
import datetime
import yfinance as yf
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.model_selection import train_test_split, cross_val_score, StratifiedKFold
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import GridSearchCV
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from imblearn.over_sampling import SMOTE
from sklearn.model_selection import RandomizedSearchCV
from imblearn.over_sampling import ADASYN
from xgboost import XGBClassifier
import xgboost as xgb
import pytz
from sklearn.preprocessing import MinMaxScaler
from imblearn.over_sampling import BorderlineSMOTE
from sklearn.decomposition import PCA
from sklearn.metrics import roc_auc_score
from sklearn.feature_selection import SelectFromModel
import tensorflow as tf
from tensorflow import keras
from keras import layers, callbacks
from sklearn.utils.class_weight import compute_class_weight
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.pipeline import Pipeline
from tensorflow.keras.optimizers.legacy import Adam
from tensorflow.keras.layers import Dense, BatchNormalization, Dropout
from tensorflow.keras.regularizers import l2
from sklearn.ensemble import VotingClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.tree import DecisionTreeClassifier
from keras.models import Sequential
import keras_tuner as kt
from kerastuner.tuners import RandomSearch
import joblib
import itertools
import lightgbm as lgb

/var/folders/zc/z8rbpqpj3s38f0x8wmhkq0lh0000gn/T/ipykernel_17868/3810277901.py:39: DeprecationWarning: `import kerastuner` is deprecated, please use `import keras_tuner`.
  from kerastuner.tuners import RandomSearch


### Helper Functions

In [2]:
def next_four_fridays():
    # Get today's date and time in EST timezone
    est = pytz.timezone('US/Eastern')
    today = dt.now(est)
    
    # Find the next Friday
    days_until_friday = (4 - today.weekday() + 7) % 7
    next_friday = today + timedelta(days=days_until_friday)
    
    # Reset the time to 4:30 PM on the next Friday
    next_friday = next_friday.replace(hour=16, minute=30, second=0, microsecond=0)
    
    # If today is Friday and it's past 4:30 PM, consider the next week's Friday
    if today.weekday() == 4 and today.time() > next_friday.time():
        next_friday += timedelta(days=7)
    
    # Remove time from datetime for output
    next_friday = next_friday.date()
    
    # Find the Friday after the next
    following_friday = next_friday + timedelta(days=7)
    
    # Find the Friday after the following
    next_next_friday = following_friday + timedelta(days=7)
    
    # Find the Friday after the next next
    next_next_next_friday = next_next_friday + timedelta(days=7)
    
    return next_friday.strftime('%Y-%m-%d'), following_friday.strftime('%Y-%m-%d'), next_next_friday.strftime('%Y-%m-%d'), next_next_next_friday.strftime('%Y-%m-%d')

# Get the next four Fridays
friday1, friday2, friday3, friday4 = next_four_fridays()
print(f"The next four Fridays are: {friday1}, {friday2}, {friday3}, and {friday4}")

The next four Fridays are: 2024-03-01, 2024-03-08, 2024-03-15, and 2024-03-22


# Viewing option chains

In [3]:
print(friday1)

2024-03-01


In [4]:
file_viewer = pd.read_csv('Data/naked_puts_results.csv')
filtered_data = file_viewer[file_viewer['Expiration Date'] == friday1]

# Display all rows, no limit
pd.set_option('display.max_rows', None)
# Display all columns, no limit
pd.set_option('display.max_columns', None)

filtered_data['ROI (%)'] = filtered_data['ROI (%)'].astype(float)
# filter out rows with ROI (%) greater than 0.8
# filtered_data = filtered_data[filtered_data['ROI (%)'] > 0.8]
# filter out rows with strike price less than 6
# filtered_data = filtered_data[filtered_data['strike'] <= 7]

# sort by ROI (%) in ascending order
filtered_data = filtered_data.sort_values(by=['ROI (%)'], ascending=False)

# Show only the columns 'Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)', 'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', and '52WeekLow'
filtered_data = filtered_data[['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 'ROI (%)', 'OTM (%)', 'Implied Volatility', 'volume', 'openInterest', 'highPrice', 'Original Stock Price', 'Original ROI (%)',
    'Original OTM (%)', '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP', '52WeekHigh', '52WeekLow']]

# Show only the top 10 rows
filtered_data.head(20)

Expiration Date   ETF  Stock Price   bid  strike  ROI (%)  OTM (%)  \
5        2024-03-01   ACB         3.26  0.09     0.5    21.95    84.66   
127      2024-03-01   PCT         5.55  0.60     5.5    12.24     0.90   
126      2024-03-01   PCT         5.55  0.45     5.0     9.89     9.91   
130      2024-03-01  PLUG         3.01  0.25     3.0     9.09     0.33   
174      2024-03-01    WW         3.17  0.25     3.0     9.09     5.36   
59       2024-03-01   FSR         0.59  0.04     0.5     8.70    15.25   
104      2024-03-01  LAZR         2.19  0.15     2.0     8.11     8.68   
138      2024-03-01  RDFN         6.89  0.40     6.5     6.56     5.66   
94       2024-03-01    IQ         3.51  0.19     3.5     5.74     0.28   
118      2024-03-01  NVAX         5.29  0.27     5.0     5.71     5.48   
49       2024-03-01  CLSK        16.43  0.85    16.0     5.61     2.62   
4        2024-03-01  AAOI        14.15  0.70    14.0     5.26     1.06   
16       2024-03-01   ALT         9.20  0.45     9.0     5.26     2.17   
41       2024-03-01  CIFR         3.03  0.15     3.0     5.26     0.99   
106      2024-03-01  LCID         3.02  0.15     3.0     5.26     0.66   
25       2024-03-01  APLD         4.04  0.20     4.0     5.26     0.99   
33       2024-03-01  BITF         3.02  0.15     3.0     5.26     0.66   
96       2024-03-01  IREN         6.18  0.30     6.0     5.26     2.91   
172      2024-03-01  WULF         2.03  0.10     2.0     5.26     1.48   
156      2024-03-01  SPCE         1.65  0.07     1.5     4.90     9.09   

     Implied Volatility  volume  openInterest  highPrice  \
5                 11.56    82.0         153.0       0.09   
127                2.23     4.0          44.0       0.60   
126                2.31   343.0        1033.0       0.45   
130                1.47  7800.0        4887.0       0.25   
174                1.95   388.0         360.0       0.25   
59                 2.94  3116.0        6977.0       0.04   
104                1.94  2234.0         499.0       0.15   
138                1.52    40.0         779.0       0.40   
94                 0.99    16.0          81.0       0.19   
118                1.38   891.0         329.0       0.27   
49                 1.18  1659.0        1666.0       0.85   
4                  1.08    99.0          53.0       0.70   
16                 1.11   153.0         160.0       0.45   
41                 1.06   147.0         732.0       0.15   
106                0.93  3695.0        4111.0       0.15   
25                 1.15  3058.0          76.0       0.20   
33                 1.04   211.0         716.0       0.15   
96                 1.21   450.0          68.0       0.30   
172                1.17   262.0        1748.0       0.10   
156                1.47   587.0        1628.0       0.07   

     Original Stock Price  Original ROI (%)  Original OTM (%)  50-day MA  \
5                    3.26             21.95             84.66       4.30   
127                  5.55             12.24              0.90       4.04   
126                  5.55              9.89              9.91       4.04   
130                  3.01              9.09              0.33       4.01   
174                  3.17              9.09              5.36       5.81   
59                   0.59              8.70             15.25       1.06   
104                  2.19              8.11              8.68       2.86   
138                  6.89              6.56              5.66       8.64   
94                   3.51              5.74              0.28       4.03   
118                  5.29              5.71              5.48       4.53   
49                  16.43              5.61              2.62      10.87   
4                   14.15              5.26              1.06      19.24   
16                   9.20              5.26              2.17       9.69   
41                   3.03              5.26              0.99       3.34   
106                  3.02              5.26     

In [5]:
# Read in data
df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Define function to color rows 
def color_row(row):
    color = 'lightgreen' if row['Status'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Filter columns to keep
columns = ['Expiration Date', 'ETF', 'Original Stock Price', 'Stock Price', 'strike', 'volume',  
           'openInterest', 'highPrice', 'Original ROI (%)', 'Original OTM (%)',
           '50-day MA', '100-day MA', '200-day MA', 'RSI', 'MACD', 'VWAP',
           '52WeekHigh', '52WeekLow', 'Status']


df = df[columns].sort_values('Expiration Date', ascending=False).head(100)
# Take top 100 rows ordered by Original ROI (%)
df = df.sort_values('Original ROI (%)', ascending=False).head(100)

# Style DataFrame 
styled_df = (df.style  
             .applymap(lambda x: 'color: black') # Set text color
             .apply(color_row, axis=1) # Set row colors
             .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns))

# Display DataFrame 
styled_df

In [6]:
# Load the CSV file into a DataFrame
from sklearn.impute import SimpleImputer


df = pd.read_csv('Data/putsDataSuccessFailed.csv')

# Save the columns to be dropped for later use
retained_columns = df[['contractSymbol', 'Expiration Date', 'ETF']]

# Data Preprocessing
df.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)
df = pd.get_dummies(df, columns=['recommendationKey'], drop_first=True)

# Handle missing values with imputation
imputer = SimpleImputer(strategy='mean')
X = df.drop('Status', axis=1)
y = df['Status']

# Encode the target variable 'Status'
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)

X_imputed = imputer.fit_transform(X)

# Address class imbalance with SMOTE
smote = SMOTE(random_state=42)
X_resampled, y_resampled = smote.fit_resample(X_imputed, y_encoded)

# Split the data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_resampled, y_resampled, test_size=0.2, random_state=42)

# Model Selection and Hyperparameter Tuning (LightGBM)
param_grid = {
    'n_estimators': [100, 200, 300],
    'max_depth': [3, 4, 5],
    'learning_rate': [0.05, 0.1, 0.2]
}

# Use GridSearchCV for hyperparameter tuning
lgb_classifier = lgb.LGBMClassifier(random_state=42)
grid_search = GridSearchCV(lgb_classifier, param_grid, cv=10, scoring='accuracy', n_jobs=-1)
grid_search.fit(X_train, y_train)

best_lgb_model = grid_search.best_estimator_

# Save the best model and other objects
joblib.dump(best_lgb_model, 'best_lgb_model.joblib')
joblib.dump(label_encoder, 'label_encoder.joblib')
joblib.dump(imputer, 'imputer.joblib')

# Load new data
new_data = pd.read_csv('Data/naked_puts_results.csv')

# Save the columns to be dropped from new data for later use
new_retained_columns = new_data[['contractSymbol', 'Expiration Date', 'ETF']]

# Preprocess new data as per training data
new_data.drop(['contractSymbol', 'Expiration Date', 'ETF'], axis=1, inplace=True)
new_data_encoded = pd.get_dummies(new_data, columns=['recommendationKey'], drop_first=True)

# Align columns of new data with training data
missing_cols = set(X.columns) - set(new_data_encoded.columns)
extra_cols = set(new_data_encoded.columns) - set(X.columns)
for c in missing_cols:
    new_data_encoded[c] = 0
new_data_encoded.drop(extra_cols, axis=1, inplace=True)
new_data_encoded = new_data_encoded[X.columns]

# Impute missing values
new_data_imputed = joblib.load('imputer.joblib').transform(new_data_encoded)

# Load the saved model and make predictions
loaded_model = joblib.load('best_lgb_model.joblib')
new_predictions = loaded_model.predict(new_data_imputed)

# Add predictions to the new data
new_data_with_predictions = new_data_encoded.copy()
new_data_with_predictions['Guess'] = joblib.load('label_encoder.joblib').inverse_transform(new_predictions)

# Reverse one-hot encoding to get original 'recommendationKey' column
def reverse_one_hot(df, original_column_prefix):
    one_hot_cols = [col for col in df if col.startswith(original_column_prefix)]
    df[original_column_prefix] = df[one_hot_cols].idxmax(axis=1).str.replace(original_column_prefix + '_', '')
    df.drop(one_hot_cols, axis=1, inplace=True)
    return df

new_data_with_predictions = reverse_one_hot(new_data_with_predictions, 'recommendationKey')

# Add back the retained columns to the new data with predictions
new_data_with_predictions = pd.concat([new_retained_columns.reset_index(drop=True), new_data_with_predictions.reset_index(drop=True)], axis=1)

# Save the new data with predictions
new_data_with_predictions.to_csv('Data/new_data_with_predictions.csv', index=False)

# Model Evaluation
y_pred = best_lgb_model.predict(X_test)
accuracy = accuracy_score(y_test, y_pred)
report = classification_report(y_test, y_pred)

print(f'Best LightGBM Model: {best_lgb_model}')
print(f'Accuracy: {accuracy}')
print(report)

[LightGBM] [Info] Number of positive: 680, number of negative: 683
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.004034 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 8431
[LightGBM] [Info] Number of data points in the train set: 1363, number of used features: 36
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.498899 -> initscore=-0.004402
[LightGBM] [Info] Start training from score -0.004402
[LightGBM] [Info] Number of positive: 680, number of negative: 683
[LightGBM] [Info] Number of positive: 680, number of negative: 683
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.011365 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Number of positive: 681, number of negative: 683
[LightGBM] [Info] To

In [7]:
# Read in data 
df = pd.read_csv('Data/new_data_with_predictions.csv')

# Sort by Original ROI column  
df = df.sort_values(by='Original ROI (%)', ascending=False)  

# Filter to top 300 rows
df = df.head(300)

# Filter columns to show
columns = ['Expiration Date', 'ETF', 'Stock Price', 'bid', 'strike', 
           'ROI (%)', 'OTM (%)', 'recommendationKey', 'targetLowPrice', 'targetMeanPrice', 'targetHighPrice', 'Guess']
df = df[columns]

# Define row color function
def color_row(row):
    color = 'lightgreen' if row['Guess'] == 'Success' else 'lightcoral'
    return ['background-color: %s' % color]*len(row)

# Apply cell and row styling
styled_df = (df.style
                .applymap(lambda x: 'color: black') # Black text
                .apply(color_row, axis=1) # Color rows
                .format('{:.2f}', subset=df.select_dtypes(include=['float64']).columns)) 

# Display styled DataFrame
styled_df